In [1]:
import os
import pandas as pd
import xml.etree.ElementTree as et
import re

In [28]:
columns = ['url',
            'brief_title',
            'phase',
            'agency',
            'overall_status',
            'study_first_submitted',
            'last_update_submitted'
           ]

In [29]:
df = pd.DataFrame()

In [44]:
directory = "/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT00XX"
for root, dirs, files in os.walk("/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX"):
    for file in files[1:]:
        xml = os.path.join(root, file)
        xtree = et.parse(xml)
        xroot = xtree.getroot() 
        features = {}
        for col in columns:
            for elem in xroot.iter(col):
                features[col] = elem.text
        drugs = []
        for node in xroot:
            drug = node.find('./intervention_name')
            if drug is not None:
                drugs.append(drug.text) 
        features['drugs'] = drugs
        df = df.append(features, ignore_index=True)   

In [45]:
df.to_csv("/Users/kim/Documents/Python/Press release project/Clinical_gov_NCT00XX.txt",
            sep = "\t",
           index = False)

In [46]:
df.tail(50)

agency  \
380670                                           Allergan   
380671                                  Rodolfo Alejandro   
380672                                  Rodolfo Alejandro   
380673                       Assaf-Harofeh Medical Center   
380674                 Food and Drug Administration (FDA)   
380675                                     Fresenius Kabi   
380676                  Physiotherapy Research Foundation   
380677                             University of Michigan   
380678                                       Region Skane   
380679                            Spring Arbor University   
380680                              Boston Medical Center   
380681                          Leatherhead Food Research   
380682                   Florida Heart Research Institute   
380683                                             Pfizer   
380684                                       Unilever R&D   
380685                                     Belinda Avalos   
380686                                      Atrium Health   
380687                                            Celgene   
380688                              Hung Kaung University   
380689                    Universitair Ziekenhuis Brussel   
380690                      University Hospital, Grenoble   
380691           Centre Hospitalier Universitaire, Amiens   
380692                                University of Parma   
380693                                    Aix Scientifics   
380694                          Peregrine Pharmaceuticals   
380695                                  Dexa Medica Group   
380696                          Baylor Research Institute   
380697                         American Heart Association   
380698                             Enanta Pharmaceuticals   
380699                                           Endocyte   
380700                                    Essentia Health   
380701                                           QLT Inc.   
380702                             UCB Biopharma S.P.R.L.   
380703                            University of Sao Paulo   
380704                                   Newron Sweden AB   
380705  Eunice Kennedy Shriver National Institute of C...   
380706          Assistance Publique Hopitaux De Marseille   
380707                                    GlaxoSmithKline   
380708            University Hospital, Strasbourg, France   
380709                     Immune Tolerance Network (ITN)   
380710                    National Cancer Institute (NCI)   
380711                          Merz Pharmaceuticals GmbH   
380712                             St. Justine's Hospital   
380713                                Forest Laboratories   
380714                                            Mei Shi   
380715              University of California, Los Angeles   
380716                                    Gazi University   
380717                                             Pfizer   
380718                               Bristol-Myers Squibb   
380719             The Leeds Teaching Hospitals NHS Trust   

                                              brief_title  \
380670  A Study of GANFORT® UD in Patients With Primar...   
380671  Prevention of de Novo Allosensitization in Isl...   
380672  Long Term Follow up of Recipients of Functiona...   
380673  Follow up of Patients After Oral Immunotherapy...   
380674  Correlation of Mesalamine Pharmacokinetics Wit...   
380675  Pilot Study Efficacy and Tolerance Fish Oil Em...   
380676  Safety and Efficacy of Emergency On-call Respi...   
380677                      EoE(Eosinophilic Esophagitis)   
380678  The Swedish Study on Paleolithic Diet for Type...   
380679                NMES Efficacy on Patients With NBPP   
380680  Novel Biophotonics Methodology for Colon Cance...   
380681  Gut Hormone Response After Paleolithic-type Meals   
380682                  Contrast Nephropathy and Nitrates   
380683  The Effects of Prazosin on Dopamine in Healthy...   
380684   Post-prandial G

In [55]:
sponsors = df.agency.value_counts().rename_axis('sponsor').reset_index(name='trials')

In [68]:
sponsors.to_csv("/Users/kim/Documents/Python/Press release project/Clinical_sponsors_table_20201101.txt",
            sep = "\t",
           index = False)

In [57]:
sponsors.head()

sponsor  trials
0  National Cancer Institute (NCI)    8810
1                  GlaxoSmithKline    6615
2                           Pfizer    5130
3         Novartis Pharmaceuticals    4030
4        Merck Sharp & Dohme Corp.    3695

In [25]:
Tick_table = "/Users/kim/Documents/Python/Press release project/Stock_lists_20201031.txt"
## function to find share tick by company name using text as input
def tick_finder(string):
    # https://topforeignstocks.com/stock-lists
    tick = pd.read_csv(Tick_table, encoding ='latin1', sep = '\t')
    tick['Company'] = tick['Company'].str.lower()
    tick['first_w'] = tick['Company'].str.split(r"\s|'|,|-").map(lambda x:x[0])
    string = str(string)
    mylist = re.split(r"\s|'|’|,|-", string)
    ticker = tick['Ticker'][tick.first_w.isin(mylist)]
    if len(ticker) > 0:
        return(ticker.to_string(index = False))
    else:
        return('')

In [26]:
sponsors = pd.read_csv("/Users/kim/Documents/Python/Press release project/Clinical_sponsors_table_20201101.txt", encoding ='latin1', sep = '\t')

In [27]:
sponsors.sponsor = sponsors.sponsor.str.lower()

In [28]:
sponsors.sponsor = sponsors.sponsor.str.replace('united therapeutics', 'unitedtherapeutics')
sponsors.sponsor = sponsors.sponsor.str.replace('la jolla pharmaceutical', 'lajollapharmaceutical')

In [29]:
sponsors['Tick'] = sponsors.sponsor.map(tick_finder)

In [30]:
sponsors.Tick = sponsors.Tick.str.replace(' ', '').str.split('\n')

In [31]:
duplication = sponsors.loc[sponsors.Tick.str.len() > 1]
#sponsors.Tick = df1.Tick.map(lambda x : x[0])

In [32]:
conflict = duplication.Tick.map(lambda x : x[0] != x[1])

In [33]:
duplication.loc[conflict.to_numpy()]

sponsor  trials  \
316           medtronic cardiac rhythm and heart failure     185   
681                         campus bio-medico university      85   
682                                   medtronic vascular      85   
920         walter reed national military medical center      60   
944             deutsche krebshilfe e.v., bonn (germany)      60   
...                                                  ...     ...   
12664                                    takara bio inc.       5   
12677           emergent product development seattle llc       5   
12744       251 hellenic air force & va general hospital       5   
12884              sino medical sciences technology inc.       5   
13051  evandro chagas research institute, bio-manguin...       5   

                                       Tick  
316                             [MDT, RYTM]  
681                       [BPTH, BIO, TECH]  
682                             [MDT, VBLT]  
920                             [WTB, WTB3]  
944    [DBK, DB1, DEQ, DFV, JB7, DPW, DWNI]  
...                                     ...  
12664                     [BPTH, BIO, TECH]  
12677                           [EBS, SGEN]  
12744                            [AB1, VQT]  
12884                          [SBHMY, SGU]  
13051                     [BPTH, BIO, TECH]  

[137 rows x 3 columns]

In [34]:
## sponsors without tick duplication
sponsorsSingleTick = sponsors.loc[sponsors.Tick.str.len() == 1]

In [35]:
sponsorsSingleTick.Tick = sponsorsSingleTick.Tick.map(lambda x : x[0])

/Users/kim/anaconda3/envs/Press_Release_TF_project/lib/python3.7/site-packages/pandas/core/generic.py:5303: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self[name] = value


In [36]:
sponsorsSingleTick = sponsorsSingleTick.loc[sponsorsSingleTick.Tick != ""]

In [37]:
sponsorsSingleTick.shape

(1119, 3)

In [38]:
sponsorsSingleTick2 = sponsorsSingleTick.groupby('Tick', as_index= False)['trials'].sum()

In [39]:
sponsorsSingleTick2.shape

(468, 2)

In [40]:
sponsorsSingleTick2.to_csv("/Users/kim/Documents/Python/Press release project/Tick_Trials_20201110.txt",
            sep = "\t",
           index = False)

In [41]:
tick = pd.read_csv(Tick_table, encoding ='latin1', sep = '\t')

In [44]:
companyInfos = tick.merge(sponsorsSingleTick2, how = 'left', left_on = 'Ticker', right_on = 'Tick')

In [45]:
companyInfos.head(20)

Company Ticker  Market                  Sector  \
0      1+1 DRILLISCH AG O.N.    DRI     FRA          Communications   
1               10x Genomics    TXG  NASDAQ             Health Care   
2       11 88 0 SOLUTIONS AG    TGT     FRA              Technology   
3               2G ENERGY AG    2GB     FRA                  Energy   
4              3U HOLDING AG    UUU     FRA             Industrials   
5                     4SC AG    VSC     FRA             Health Care   
6     7C SOLARPARKEN AG O.N.   HRPK     FRA                  Energy   
7                      89bio   ETNB  NASDAQ             Health Care   
8     A.A.A.AG ALLG.ANL.VERW    AAA     FRA             Real Estate   
9                  A.I.S. AG    LUM     FRA             Industrials   
10   A.S.CREATION TAPETEN NA   ACWN     FRA  Consumer Discretionary   
11         A.SPRINGER SE VNA    SPR     FRA          Communications   
12         AAP IMPLANTATE AG    AAQ     FRA             Health Care   
13            AAREAL BANK AG    ARL     FRA              Financials   
14       Abbott Laboratories    ABT    NYSE             Health Care   
15               AbbVie Inc.   ABBV    NYSE             Health Care   
16                     Abcam  ABCZY    Else                     NaN   
17  Abeona Therapeutics Inc.   ABEO  NASDAQ             Health Care   
18                    Ablynx  ABYLY    Else                     NaN   
19              AC Immune SA   ACIU  NASDAQ             Health Care   

                          Industry                  SubIndustry     Founded  \
0               Telecommunications           Telecommunications    02/09/04   
1                      Health Care  Medical Equipment & Devices    07/02/12   
2         Software & Tech Services          Technology Services    08/01/18   
3                 Renewable Energy             Renewable Energy  01/25/2008   
4              Industrial Products         Electrical Equipment  07/17/2003   
5                      Health Care             Biotech & Pharma  08/30/2000   
6                 Renewable Energy             Renewable Energy  01/26/2015   
7                      Health Care             Biotech & Pharma  06/28/2019   
8                      Real Estate         Real Estate Services    07/12/04   
9              Industrial Services  Commercial Support Services  01/25/2005   
10  Retail & Whsle - Discretionary    Wholesale - Discretionary    04/08/98   
11                           Media    Publishing & Broadcasting  05/19/1970   
12                     Health Care  Medical Equipment & Devices    09/10/97   
13              Financial Services            Specialty Finance  03/17/2003   
14                     Health Care  Medical Equipment & Devices  03/06/1900   
15                     Health Care             Biotech & Pharma    04/10/12   
16                             NaN                          NaN         NaN   
17                     Health Care             Biotech & Pharma  06/22/1989   
18                             NaN                          NaN         NaN   
19                     Health Care             Biotech & Pharma  02/13/2003   

                                              Address               Phone  \
0   Wilhelm Roentgen Strasse 1-5 Maintal, 63477 Ge...     49-6181-412-143   
1   6230 Stoneridge Mall Road Pleasanton, CA 94566...      1-925-401-7300   
2         Hohenzollernstrasse 24 Essen, 45128 Germany       49-201-8099-0   
3                 Benzstrasse 3 Heek, D 48619 Germany      49-2568-9347-0   
4   Frauenbergstrasse 31ä£ 1/64 5/1633 Marburg, 3...       49-6421-999-0   
5         Fraunhoferstrasse 22 Planegg, 82152 Germany     49-89-7007-63-0   
6      An der Feuerwache 15 Bayreuth, D-95445 Germany  49-921-23-05-57-77   
7   535 Mission Street 14th Floor San Francisco, C...      1-415-500-4614   
8   Friedrich -Ebert Plant 3 Frankfurt Am Main, 60...     49-69-2400-0815   
9           Im Bettenklingen 6 69488 Birkenau Germany      49-6201-393895   
10        Suedstrasse 

In [46]:
companyInfos.shape

(1316, 13)

In [47]:
companyInfos.to_csv("/Users/kim/Documents/Python/Press release project/Company_Info_20201110.txt",
            sep = "\t",
           index = False)

In [82]:
Tick_table = "/Users/kim/Documents/Python/Press release project/Stock_lists_20201031.txt"
Company_Infos = pd.read_csv(Tick_table, encoding ='latin1', sep = '\t')
Company_Infos['Company'] = Company_Infos['Company'].str.lower()
Company_Infos['first_w'] = Company_Infos['Company'].str.split(r"\s|'|,").map(lambda x:x[0])

In [88]:
def TrialMatcher(string):
    string = str(string)
    mylist = re.split(r"\s|'|’|,|-", string)
    print(mylist)
    num_trials = int(sponsors['trials'][sponsors.sponsor.isin(mylist)])
    if len(ticker) > 0:
        return(ticker.to_string(index = False))
    else:
        return('')

In [97]:
num_trials = sponsors['trials'][sponsors.sponsor.isin(['Schuler'])]

In [98]:
int(num_trials)

TypeError: cannot convert the series to <class 'int'>

In [ ]:
Company_Infos['trial'] = Company_Infos.first_w.str.lower().map(TrialMatcher)

In [27]:
Tick_table = "Stock_lists_20201031.txt"
## function to find share tick by company name using text as input
def tick_finder(string):
    # https://topforeignstocks.com/stock-lists
    tick = pd.read_csv(Tick_table, encoding ='latin1', sep = '\t')
    tick['Company'] = tick['Company'].str.lower()
    tick['first_w'] = tick['Company'].str.split(r"\s|'|,").map(lambda x:x[0])
    string = str(string)
    mylist = re.split(r"\s|'|’|,|-", string)
    ticker = tick['Ticker'][tick.first_w.isin(mylist)]
    if len(ticker) > 0:
        return(ticker.to_string(index = False))
    else:
        return('')
    

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/.DS_Store
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000012.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000025.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000038.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000051.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000064.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000077.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000090.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000103.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0100xxxx/NCT01000116.xml
/Users/kim/Documents/Python/

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024738.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024751.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024764.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024777.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024790.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024803.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024816.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024829.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024842.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0102xxxx/NCT01024855.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045876.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045889.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045902.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045915.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045928.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045941.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045954.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045967.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045980.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0104xxxx/NCT01045993.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072097.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072110.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072123.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072136.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072149.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072162.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072175.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072188.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072201.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0107xxxx/NCT01072214.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098292.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098305.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098318.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098331.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098344.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098357.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098383.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098396.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098409.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0109xxxx/NCT01098422.xml
/Users/kim

...

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845350.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845363.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845376.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845389.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845402.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845415.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845428.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845441.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845454.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0184xxxx/NCT01845467.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871532.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871545.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871558.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871571.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871584.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871597.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871610.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871623.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871636.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0187xxxx/NCT01871649.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904227.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904240.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904253.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904266.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904279.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904292.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904305.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904318.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904331.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0190xxxx/NCT01904344.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01936948.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01936961.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01936974.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01936987.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937000.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937013.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937026.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937039.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937052.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0193xxxx/NCT01937065.xml
/Users/kim

/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969604.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969617.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969630.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969643.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969656.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969669.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969682.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969695.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969708.xml
/Users/kim/Documents/Python/Press release project/AllPublicXML/NCT01XX/NCT0196xxxx/NCT01969721.xml
/Users/kim

In [30]:
for file in os.listdir()[0:100]:
    xtree = et.parse(file)
    xroot = xtree.getroot() 
    features = {}
    for col in columns:
        for elem in xroot.iter(col):
            features[col] = elem.text       
    df = df.append(features, ignore_index=True)

In [31]:
df.head(20)

url  \
0         https://clinicaltrials.gov/show/NCT01000012   
1         https://clinicaltrials.gov/show/NCT01000025   
2         https://clinicaltrials.gov/show/NCT01000038   
3                           http://www.mdanderson.org   
4         https://clinicaltrials.gov/show/NCT01000064   
5         https://clinicaltrials.gov/show/NCT01000077   
6         https://clinicaltrials.gov/show/NCT01000090   
7         https://clinicaltrials.gov/show/NCT01000103   
8         https://clinicaltrials.gov/show/NCT01000116   
9         https://clinicaltrials.gov/show/NCT01000129   
10        https://clinicaltrials.gov/show/NCT01000142   
11        https://clinicaltrials.gov/show/NCT01000155   
12        https://clinicaltrials.gov/show/NCT01000168   
13        https://clinicaltrials.gov/show/NCT01000181   
14        https://clinicaltrials.gov/show/NCT01000194   
15  https://www.novctrd.com/CtrdWeb/displaypdf.nov...   
16        https://clinicaltrials.gov/show/NCT01000220   
17        https://clinicaltrials.gov/show/NCT01000233   
18        https://clinicaltrials.gov/show/NCT01000246   
19        https://clinicaltrials.gov/show/NCT01000259   

                                          brief_title            phase  \
0   Compassionate Use of the Becker Expander/Breas...              NaN   
1   PF-00299804 in Stage IIIB or Stage IV Non-Smal...          Phase 3   
2   Wii-fit for Activity, Balance and Gait in Assi...              N/A   
3    Eltrombopag for Post Transplant Thrombocytopenia          Phase 2   
4   Treatment of Traumatic Brain Injury (TBI)-Rela...          Phase 3   
5   Establishment of Cell Culture Systems From Dis...              NaN   
6     Surgical Versus Medical Treatment of Acromegaly              NaN   
7   Using Repetitive Transcranial Magnetic Stimula...          Phase 3   
8   Fibrin Glue Versus Tacked Fixation in Groin He...              N/A   
9                 Adaptive Planning in Bladder Cancer          Phase 2   
10  Preventative Osteopathic Manipulative Treatmen...              N/A   
11  Efficacy of Vorinostat to Induce Fetal Hemoglo...          Phase 2   
12               Treadmill Therapy and Brain Injuries              N/A   
13  Imaging 61CuATSM Uptake in Atherosclerotic Pla...              NaN   
14        Acute Fatty Acid Intervention Study (AFAST)              N/A   
15  Single-blind, Dose-ranging Study of Novel Swin...  Phase 2/Phase 3   
16        Evaluation of Omeprazole Effect on Glaucoma          Phase 1   
17  Value of Oral Phytate (InsP6) in the Preventio...  Phase 2/Phase 3   
18  Response to Influenza Virus Vaccination in Pat...              N/A   
19  Study of Tumor Tissue Samples From Patients Wh...              NaN   

                                          agency           overall_status  \
0                          Mentor Worldwide, LLC      No longer available   
1                                         Pfizer                Completed   
2                         University of Nebraska                Completed   
3                       Novartis Pharmaceuticals                Completed   
4                                          Shire               Terminated   
5            United States Department of Defense  Enrolling by invitation   
6                           University of Aarhus                Completed   
7        Assistance Publique - Hôpitaux de Paris           Unknown status   
8                    Zealand University Hospital                Completed   
9   Institute of Cancer Research, United Kingdom           Unknown status   
10      A.T. Still University of Health Sciences                Completed   
11                     Merck Sharp & Dohme Corp.               Terminated   
12                          University of Bergen                Completed   
13     Guy's and St Thomas' NHS Foundation Trust                Suspended   
14                Dutch Dairy Organization (NZO)                Completed   
15                             Novartis Vaccines                C

In [33]:
xtree = et.parse('NCT01000025.xml')
xroot = xtree.getroot() 

In [80]:
print(xroot.find('./intervention_name'))

None


In [83]:
for node in xroot:
    s = node.find('./intervention_name')
    if s is not None:
        print(s.text)

PF-00299804
Placebo


In [87]:
drugs = []
for node in xroot:
    s = node.find('./intervention_name')
    if s is not None:
        drugs.append(s.text)

In [88]:
drugs

['PF-00299804', 'Placebo']

In [69]:
if xroot.find('./intervention_name') is not None:
  drugs = [drug.text for drug in xroot.findall('./intervention_name')]

In [70]:
drugs

["<Element 'intervention_name' at 0x1136d8890>",
 "<Element 'intervention_name' at 0x1136d8830>"]

In [33]:
tree = lxml.etree.parse("small.xml")
pretty = lxml.etree.tostring(tree, encoding="unicode", pre

SyntaxError: unexpected EOF while parsing (<ipython-input-33-13ef69eb02bb>, line 2)

In [ ]:
df_cols = ["name", "email", "grade", "age"]
rows = []

for node in xroot: 
    s_name = node.attrib.get("name")
    s_mail = node.find("email").text if node is not None else None
    s_grade = node.find("grade").text if node is not None else None
    s_age = node.find("age").text if node is not None else None
    
    rows.append({"name": s_name, "email": s_mail, 
                 "grade": s_grade, "age": s_age})

out_df = pd.DataFrame(rows, columns = df_cols)

In [99]:
'kim' in ['kim', 'tim', 'jim']

True

In [100]:
names = ['kim', 'tim', 'jim']
days = ['Mon', 'Tues']

In [106]:
string = "Mon"
for i in range(0, len([names, days])):
    if string in [names, days][i]:
        num = i
print(num)

1


In [105]:
num

0